In [1]:
# Ejercicio de practica para generar un etiquetador de
#partes de la oracion basado en un HMM
# Este ejemplo fue diseñado por Katrin Erk. 


import nltk
import sys
from nltk.corpus import brown # corpus en ingles etiquetado con POS tags


In [2]:
# Generar lista de pares etiqueta/palabra
brown_word_tags = []
print(type(brown.tagged_sents()))  #python 2 print type(brown.tagged_sents)

<class 'nltk.corpus.reader.util.ConcatenatedCorpusView'>


In [3]:
print (len(brown.tagged_sents()))

57340


In [4]:
print (brown.tagged_sents()[1])

[('The', 'AT'), ('jury', 'NN'), ('further', 'RBR'), ('said', 'VBD'), ('in', 'IN'), ('term-end', 'NN'), ('presentments', 'NNS'), ('that', 'CS'), ('the', 'AT'), ('City', 'NN-TL'), ('Executive', 'JJ-TL'), ('Committee', 'NN-TL'), (',', ','), ('which', 'WDT'), ('had', 'HVD'), ('over-all', 'JJ'), ('charge', 'NN'), ('of', 'IN'), ('the', 'AT'), ('election', 'NN'), (',', ','), ('``', '``'), ('deserves', 'VBZ'), ('the', 'AT'), ('praise', 'NN'), ('and', 'CC'), ('thanks', 'NNS'), ('of', 'IN'), ('the', 'AT'), ('City', 'NN-TL'), ('of', 'IN-TL'), ('Atlanta', 'NP-TL'), ("''", "''"), ('for', 'IN'), ('the', 'AT'), ('manner', 'NN'), ('in', 'IN'), ('which', 'WDT'), ('the', 'AT'), ('election', 'NN'), ('was', 'BEDZ'), ('conducted', 'VBN'), ('.', '.')]


In [6]:
# Agregar START/END a las oraciones del corpus
for sent in brown.tagged_sents():
    brown_word_tags.append( ("START", "START") )  # Agregar palabra, etiqueta especial
    # Acortar las etiquetas para hacer un conjunto mas general
    brown_word_tags.extend([ (tag[:2], word) for (word, tag) in sent ])
    # Agregar palabra/etiqueta especal END
    brown_word_tags.append( ("END", "END") )
    
    

In [9]:
brown_word_tags[0:40]

[('START', 'START'),
 ('AT', 'The'),
 ('NP', 'Fulton'),
 ('NN', 'County'),
 ('JJ', 'Grand'),
 ('NN', 'Jury'),
 ('VB', 'said'),
 ('NR', 'Friday'),
 ('AT', 'an'),
 ('NN', 'investigation'),
 ('IN', 'of'),
 ('NP', "Atlanta's"),
 ('JJ', 'recent'),
 ('NN', 'primary'),
 ('NN', 'election'),
 ('VB', 'produced'),
 ('``', '``'),
 ('AT', 'no'),
 ('NN', 'evidence'),
 ("''", "''"),
 ('CS', 'that'),
 ('DT', 'any'),
 ('NN', 'irregularities'),
 ('VB', 'took'),
 ('NN', 'place'),
 ('.', '.'),
 ('END', 'END'),
 ('START', 'START'),
 ('AT', 'The'),
 ('NN', 'jury'),
 ('RB', 'further'),
 ('VB', 'said'),
 ('IN', 'in'),
 ('NN', 'term-end'),
 ('NN', 'presentments'),
 ('CS', 'that'),
 ('AT', 'the'),
 ('NN', 'City'),
 ('JJ', 'Executive'),
 ('NN', 'Committee')]

In [10]:
#############################################################################
# EMPEZAMOS POR CALCULAR LAS PROBABILITIES DE EMISSION, 
#  PARAMETRO B DEL HMM HMM #
#############################################################################
# Estimating P(wi | ti) from corpus data using Maximum Likelihood Estimation (MLE):
# P(wi | ti) = count(wi, ti) / count(ti)
# conditional frequency distribution
cfd_tagwords = nltk.ConditionalFreqDist(brown_word_tags)
# conditional probability distribution usando MLE
cpd_tagwords = nltk.ConditionalProbDist(cfd_tagwords, nltk.MLEProbDist)

In [11]:
print (type(cfd_tagwords))

<class 'nltk.probability.ConditionalFreqDist'>


In [14]:
print(cfd_tagwords['NN'])

<FreqDist with 24469 samples and 227799 outcomes>


In [19]:
print(cfd_tagwords['IN'].freq('on'))

0.04761360948193587


In [20]:
print("Prob. of an adj. (JJ) being 'new' is", 
      cpd_tagwords["JJ"].prob("new"))
print("The probability of a verb (VB) being 'duck' is", 
      cpd_tagwords["VB"].prob("duck"))



Prob. of an adj. (JJ) being 'new' is 0.01472344917632025
The probability of a verb (VB) being 'duck' is 6.042713350943527e-05


In [21]:
print("The probability of a noun (NN) being 'duck' is", 
      cpd_tagwords["NN"].prob("duck"))


The probability of a noun (NN) being 'duck' is 8.779669796618949e-06


In [23]:
print("The probability of a noun (NN) being 'dog' is", 
      cpd_tagwords["NN"].prob("dog"))

The probability of a noun (NN) being 'dog' is 0.0003072884428816632


In [25]:
#############################################################################
# NOW LET'S COMPUTE THE TRANSITION PROBABILITIES, PARAMETER A OF THE HMM #
#############################################################################
# Estimating P(ti | t{i-1}) from corpus data using Maximum Likelihood Estimation (MLE):
# P(ti | t{i-1}) = count(t{i-1}, ti) / count(t{i-1})
brown_tags = [tag for (tag, word) in brown_word_tags ]



In [26]:
print(brown_tags)

['START', 'AT', 'NP', 'NN', 'JJ', 'NN', 'VB', 'NR', 'AT', 'NN', 'IN', 'NP', 'JJ', 'NN', 'NN', 'VB', '``', 'AT', 'NN', "''", 'CS', 'DT', 'NN', 'VB', 'NN', '.', 'END', 'START', 'AT', 'NN', 'RB', 'VB', 'IN', 'NN', 'NN', 'CS', 'AT', 'NN', 'JJ', 'NN', ',', 'WD', 'HV', 'JJ', 'NN', 'IN', 'AT', 'NN', ',', '``', 'VB', 'AT', 'NN', 'CC', 'NN', 'IN', 'AT', 'NN', 'IN', 'NP', "''", 'IN', 'AT', 'NN', 'IN', 'WD', 'AT', 'NN', 'BE', 'VB', '.', 'END', 'START', 'AT', 'NP', 'NN', 'NN', 'HV', 'BE', 'VB', 'IN', 'NP', 'JJ', 'NN', 'NN', 'NP', 'NP', 'TO', 'VB', 'NN', 'IN', 'JJ', '``', 'NN', "''", 'IN', 'AT', 'JJ', 'NN', 'WD', 'BE', 'VB', 'IN', 'NN', 'NP', 'NP', 'NP', '.', 'END', 'START', '``', 'RB', 'AT', 'JJ', 'NN', 'IN', 'JJ', 'NN', 'BE', 'VB', "''", ',', 'AT', 'NN', 'VB', ',', '``', 'IN', 'AT', 'JJ', 'NN', 'IN', 'AT', 'NN', ',', 'AT', 'NN', 'IN', 'NN', 'CC', 'AT', 'NN', 'IN', 'DT', 'NN', "''", '.', 'END', 'START', 'AT', 'NN', 'VB', 'PP', 'DO', 'VB', 'CS', 'AP', 'IN', 'NP', 'NN', 'CC', 'NN', 'NN', '``', 'BE',

In [27]:
# make conditional frequency distribution:
# count(t{i-1} ti)
cfd_tags= nltk.ConditionalFreqDist(nltk.bigrams(brown_tags))
# make conditional probability distribution, using
# maximum likelihood estimate:
# P(ti | t{i-1})
cpd_tags = nltk.ConditionalProbDist(cfd_tags, nltk.MLEProbDist)

In [28]:
print("Que tan probable es ver NN seguido de NN?")
print(cpd_tags['NN'].prob('NN'))

Que tan probable es ver NN seguido de NN?
0.10370545963766303


In [29]:
print("Que tan probable es ver NN seguido de NN?")
print(cpd_tags['NN'].prob('RB'))

Que tan probable es ver NN seguido de NN?
0.01913968015662931


In [30]:
#############################################################################
# NOW LET'S PUT THINGS TOGETHER #
#############################################################################
# what is the probability of the tag sequence "PP VB TO VB" for the word sequence "I want to race"?
# It is
# P(START) * P(PP|START) * P(I | PP) *
#            P(VB | PP) * P(want | VB) *
#            P(TO | VB) * P(to | TO) *
#            P(VB | TO) * P(race | VB) *
#            P(END | VB)
#
# We leave aside P(START) for now.
# We leave aside P(START) for now.

prob_tagseq = cpd_tags["START"].prob("PP") * cpd_tagwords["PP"].prob("I") * \
    cpd_tags["PP"].prob("VB") * cpd_tagwords["VB"].prob("want") * \
    cpd_tags["VB"].prob("TO") * cpd_tagwords["TO"].prob("to") * \
    cpd_tags["TO"].prob("VB") * cpd_tagwords["VB"].prob("race") * \
    cpd_tags["VB"].prob("END")

print( "The probability of the tag sequence 'START PP VB TO VB END'")
print("for 'I want to race' is:", prob_tagseq)



The probability of the tag sequence 'START PP VB TO VB END'
for 'I want to race' is: 1.0817766461150474e-14


In [31]:
prob_tagseq = cpd_tags["START"].prob("PP") * cpd_tagwords["PP"].prob("I") * \
    cpd_tags["PP"].prob("NN") * cpd_tagwords["NN"].prob("want") * \
    cpd_tags["VB"].prob("TO") * cpd_tagwords["TO"].prob("to") * \
    cpd_tags["TO"].prob("VB") * cpd_tagwords["VB"].prob("race") * \
    cpd_tags["VB"].prob("END")

print( "The probability of the tag sequence 'START PP VB TO VB END'")
print("for 'I want to race' is:", prob_tagseq)

The probability of the tag sequence 'START PP VB TO VB END'
for 'I want to race' is: 1.2155565540363366e-16
